In [121]:
import os
import numpy as np
import pandas as pd
import pickle
import quandl
from datetime import datetime,date

In [122]:
import plotly.offline as py
import plotly.graph_objs as go
import plotly.figure_factory as ff
py.init_notebook_mode(connected=True)

In [123]:
def get_quandl_data(quandl_id):
    '''Download and cache Quandle dataseries'''
    cache_path='{}.pkl'.format(quandl_id).replace('/','-')
    try:
        f=open(cache_path,'rb')
        df=pickle.load(f)
        print('Loaded {} from cache'.format(quandl_id))
    except (OSError,IOError) as e:
        print('Downloading {} from Quandl'.format(quandl_id))
        df=quandl.get(quandl_id,returns="pandas")
        df.to_pickle(cache_path)
        print('Cached {} at {}'.format(quandl_id,cache_path))
    return df    
    

In [124]:
# Pull Kraken BTC price exchange data
btc_usd_price_kraken = get_quandl_data('BCHARTS/KRAKENUSD')
btc_usd_price_kraken.head()

Loaded BCHARTS/KRAKENUSD from cache


Open       High        Low      Close  Volume (BTC)  \
Date                                                                   
2014-01-07  874.67040  892.06753  810.00000  810.00000     15.622378   
2014-01-08  810.00000  899.84281  788.00000  824.98287     19.182756   
2014-01-09  825.56345  870.00000  807.42084  841.86934      8.158335   
2014-01-10  839.99000  857.34056  817.00000  857.33056      8.024510   
2014-01-11  858.20000  918.05471  857.16554  899.84105     18.748285   

            Volume (Currency)  Weighted Price  
Date                                           
2014-01-07       13151.472844      841.835522  
2014-01-08       16097.329584      839.156269  
2014-01-09        6784.249982      831.572913  
2014-01-10        6780.220188      844.938794  
2014-01-11       16698.566929      890.671709

In [125]:
btc_usd_price_kraken.tail()

Open      High       Low     Close  Volume (BTC)  \
Date                                                               
2017-08-19  4130.000  4211.683  4002.636  4179.733   5163.253241   
2017-08-20  4184.937  4198.000  4066.000  4078.244   4318.746071   
2017-08-21  4076.001  4116.969  3996.000  4005.704   5070.671144   
2017-08-22  4007.398  4169.994  3620.000  4104.900  10243.524566   
2017-08-23  4104.900  4279.990  4081.400  4167.371   5323.325938   

            Volume (Currency)  Weighted Price  
Date                                           
2017-08-19       2.127969e+07     4121.371679  
2017-08-20       1.776844e+07     4114.258059  
2017-08-21       2.050837e+07     4044.508620  
2017-08-22       4.015047e+07     3919.595235  
2017-08-23       2.224692e+07     4179.139229

In [126]:
# Chart the BTC pricing data
btc_trace = go.Scatter(x=btc_usd_price_kraken.index, y=btc_usd_price_kraken['Weighted Price'])
py.iplot([btc_trace])

In [127]:
# Pull pricing data for 3 more BTC exhcnages
exchanges = ['COINBASE','BITSTAMP','BTCC','MTGOX','BITFINEX']

exchange_data = {}

exchange_data['KRAKEN'] = btc_usd_price_kraken

for exchange in exchanges:
    exchange_code = 'BCHARTS/{}USD'.format(exchange)
    btc_exchange_df = get_quandl_data(exchange_code)
    exchange_data[exchange] = btc_exchange_df

Loaded BCHARTS/COINBASEUSD from cache
Loaded BCHARTS/BITSTAMPUSD from cache
Loaded BCHARTS/BTCCUSD from cache
Loaded BCHARTS/MTGOXUSD from cache
Loaded BCHARTS/BITFINEXUSD from cache


In [128]:
def merge_dfs_on_column(dataframes,labels,col):
    '''Merge a single column of each dataframe into a new combined dataframe'''
    series_dict = {}
    for index in range(len(dataframes)):
        series_dict[labels[index]] = dataframes[index][col]
        
    return pd.DataFrame(series_dict)
    

In [129]:
# Merge the BTC price dataseries into a single dataframe
btc_usd_datasets = merge_dfs_on_column(list(exchange_data.values()), list(exchange_data.keys()), 'Weighted Price')

In [130]:
btc_usd_datasets.tail()

BITFINEX     BITSTAMP         BTCC     COINBASE       KRAKEN  \
Date                                                                       
2017-08-19       NaN  4030.604133  4062.586365  4096.284462  4121.371679   
2017-08-20       NaN  4054.143713  4100.581232  4105.412784  4114.258059   
2017-08-21       NaN  4007.736878  4065.310706  4021.619899  4044.508620   
2017-08-22       NaN  3894.115013  3891.137145  3903.716282  3919.595235   
2017-08-23       NaN  4147.527275  4146.032202  4152.035719  4179.139229   

            MTGOX  
Date               
2017-08-19    NaN  
2017-08-20    NaN  
2017-08-21    NaN  
2017-08-22    NaN  
2017-08-23    NaN

In [131]:
def df_scatter(df, title, seperate_y_axis=False, y_axis_label='', scale='linear', initial_hide=False):
    '''Generate a scatter plot of the entire dataframe'''
    label_arr = list(df)
    series_arr = list(map(lambda col: df[col], label_arr))
    
    layout = go.Layout(
        title=title,
        legend=dict(orientation="h"),
        xaxis=dict(type='date'),
        yaxis=dict(
            title=y_axis_label,
            showticklabels= not seperate_y_axis,
            type='log'
        )
    )
    
    y_axis_config = dict(
        overlaying='y',
        showticklabels=False,
        type=scale )
    
    visibility = 'visible'
    if initial_hide:
        visibility = 'legendonly'
        
    # Form Trace For Each Series
    trace_arr = []
    for index, series in enumerate(series_arr):
        trace = go.Scatter(
            x=series.index, 
            y=series, 
            name=label_arr[index],
            visible=visibility
        )
        
        # Add seperate axis for the series
        if seperate_y_axis:
            trace['yaxis'] = 'y{}'.format(index + 1)
            layout['yaxis{}'.format(index + 1)] = y_axis_config    
        trace_arr.append(trace)

    fig = go.Figure(data=trace_arr, layout=layout)
    py.iplot(fig)

In [132]:
# Plot all of the BTC exchange prices
df_scatter(btc_usd_datasets, 'Bitcoin Price (USD) By Exchange')

In [133]:
# Remove "0" values
btc_usd_datasets.replace(0,np.nan,inplace=True)

In [134]:
# Plot revised dataframes
df_scatter(btc_usd_datasets,'Bitcoin Price (USD) By Exchange')

In [135]:
btc_usd_datasets['MTGOX'].loc['2013-12-18':btc_usd_datasets['MTGOX'].index[-1]]=np.nan

In [136]:
# Plot with MTGOX trimmed
df_scatter(btc_usd_datasets,'Bitcoin Price (USD) By Exchange')

In [137]:
btc_usd_datasets['avg_btc_price_usd']=btc_usd_datasets.mean(axis=1)
btc_usd_datasets['ath']=btc_usd_datasets['avg_btc_price_usd']

# Calculate running ATH
day_before = btc_usd_datasets['avg_btc_price_usd'][0]

for day, price in enumerate(btc_usd_datasets['avg_btc_price_usd']):
    btc_usd_datasets['ath'][day]=max(day_before,price)
    day_before=btc_usd_datasets['ath'][day]


# Trend line
for day in range(len(btc_usd_datasets.index)):    
    btc_usd_datasets['trend'][day]=(0.049555609289685)*(1.173943455329252**(max(btc_usd_datasets.index[day].date().toordinal()-datetime(2010,10,8).toordinal(),0)**0.530640349974295))
    

Date
2017-08-19    1.0
2017-08-20    1.0
2017-08-21    1.0
2017-08-22    1.0
2017-08-23    1.0
Freq: D, Name: above_trend, dtype: float64

In [138]:
# Calculate how high we are above the trend
btc_usd_datasets['trend']=btc_usd_datasets['avg_btc_price_usd']

btc_usd_datasets['above_trend']=btc_usd_datasets['avg_btc_price_usd']/btc_usd_datasets['trend']
btc_usd_datasets['above_trend'].tail()

Date
2017-08-19    3.040849
2017-08-20    3.046110
2017-08-21    2.995875
2017-08-22    2.891130
2017-08-23    3.072712
Freq: D, Name: above_trend, dtype: float64

In [105]:
btc_trace = go.Scatter(x=btc_usd_datasets.index,y=btc_usd_datasets['avg_btc_price_usd'])
ath_trace = go.Scatter(x=btc_usd_datasets.index,y=btc_usd_datasets['ath'])
trend_trace = go.Scatter(x=btc_usd_datasets.index,y=btc_usd_datasets['trend'])
data=[btc_trace, ath_trace, trend_trace]

layout = go.Layout(
    xaxis=dict(
        type='scale',
        autorange=True
    ),
    yaxis=dict(
        type='log',
        autorange=True
    )
)

In [106]:
fig = go.Figure(data=data, layout=layout)
py.iplot(fig)

In [107]:
# Just trying to figure out how to use dataframes and add nans over a certain date range

#btc_usd_datasets['MTGOX'].iloc[range(0,3)]=np.nan
#btc_usd_datasets['MTGOX'].head()

#dec 18 2013

#btc_usd_datasets['MTGOX'].index[0]
#print(date(2013,12,18))

#btc_usd_datasets['MTGOX'].loc['2013-12-18':btc_usd_datasets['MTGOX'].index[-1]]=np.nan
#date_test=datetime(2010,10,8)-datetime(2010,10,7)
#date_test
#datetime(2010,10,8).timestamp()-datetime(2010,10,7).timestamp()
#datetime(2010,10,8).toordinal()-datetime(2010,10,7).toordinal()

##btc_usd_datasets['trend']=btc_usd_datasets['avg_btc_price_usd']


##for day in range(len(btc_usd_datasets.index)):
    #btc_usd_datasets.index[0].date().toordinal()-datetime(2010,10,8).toordinal()
    
    ##btc_usd_datasets['trend'][day]=(0.049555609289685)*(1.173943455329252**(max(btc_usd_datasets.index[day].date().toordinal()-datetime(2010,10,8).toordinal(),0)**0.530640349974295))
    
    #btc_usd_datasets['trend'][day]=(0.049555609289685)*1.173943455329252**(btc_usd_datasets.index[day].date().toordinal()-datetime(2010,10,8).toordinal())
    #btc_usd_datasets.index[day].date().toordinal()-datetime(2010,10,8).toordinal()
                                                        


In [108]:
def get_json_data(json_url,cache_path):
    '''Download and cache JSON data, return as a dataframe.'''
    try:
        f=open(cache_path, 'rb')
        df=pickle.load(f)
        print('Loaded {} from cache'.format(json_url))
    except (OSError, IOError) as e:
        print('Downloading {}'.format(json_url))
        df=pd.read_json(json_url)
        df.to_pickle(cache_path)
        print('Cached {} at {}'.format(json_url,cache_path))
    return df
    
        

In [109]:
base_polo_url = 'https://poloniex.com/public?command=returnChartData&currencyPair={}&start={}&end={}&period={}'
start_date=datetime.strptime('2015-01-01','%Y-%m-%d')
end_date=datetime.now()
period=86400 # pull daily data (86,400 seconds per day)

def get_crypto_data(poloniex_pair):
    '''Retrieve cryptocurrency data from polo'''
    json_url=base_polo_url.format(poloniex_pair,start_date.timestamp(),end_date.timestamp(),period)
    data_df=get_json_data(json_url,poloniex_pair)
    data_df=data_df.set_index('date')
    return data_df

In [110]:
coins=['ETH','BCH','DASH','XMR','STR','XRP','NXT']
coin_data={}

for coin in coins:
    coinpair='BTC_{}'.format(coin)
    crypto_price_df=get_crypto_data(coinpair)
    coin_data[coin]=crypto_price_df
    

Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_ETH&start=1420088400.0&end=1503715185.391205&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_BCH&start=1420088400.0&end=1503715185.391205&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_DASH&start=1420088400.0&end=1503715185.391205&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_XMR&start=1420088400.0&end=1503715185.391205&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_STR&start=1420088400.0&end=1503715185.391205&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_XRP&start=1420088400.0&end=1503715185.391205&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_NXT&start=1420088400.0&end=1503715185.391205&period=8

In [111]:
coin_data['ETH'].tail()

close      high       low      open    quoteVolume  \
date                                                                
2017-08-20  0.073525  0.073710  0.070400  0.070690  100756.634696   
2017-08-21  0.080500  0.087044  0.071717  0.073500  491598.852480   
2017-08-22  0.076602  0.086280  0.075364  0.080500  287084.551159   
2017-08-23  0.076590  0.079350  0.075000  0.076576  138264.051896   
2017-08-24  0.075935  0.077450  0.075305  0.076580   11247.530968   

                  volume  weightedAverage  
date                                       
2017-08-20   7213.589872         0.071594  
2017-08-21  39587.121362         0.080527  
2017-08-22  23005.807952         0.080136  
2017-08-23  10637.593564         0.076937  
2017-08-24    857.215647         0.076214

In [112]:
# Calculate USD Price as a new column in each altcoin dataframe
for coin in coin_data.keys():
    coin_data[coin]['price_usd']=coin_data[coin]['weightedAverage']*btc_usd_datasets['avg_btc_price_usd']

In [113]:
# Merge USD price of each altcoin into single dataframe 
combined_df=merge_dfs_on_column(list(coin_data.values()),list(coin_data.keys()),'price_usd')

In [114]:
# Add BTC price to the dataframe
combined_df['BTC'] = btc_usd_datasets['avg_btc_price_usd']

In [115]:
# Plot all prices
df_scatter(combined_df,'Cryptocurrency Prices (USD)',seperate_y_axis=False,y_axis_label='Coin Value(USD)',scale='log')

In [116]:
# Calculate correlation coefficients for 2016
combined_df_2016 = combined_df[combined_df.index.year == 2016]
combined_df_2016.pct_change().corr(method='pearson')

BCH      DASH       ETH       NXT       STR       XMR       XRP  \
BCH   NaN       NaN       NaN       NaN       NaN       NaN       NaN   
DASH  NaN  1.000000  0.115725  0.060816  0.055744  0.123248  0.087309   
ETH   NaN  0.115725  1.000000  0.020085  0.028999  0.084889  0.078307   
NXT   NaN  0.060816  0.020085  1.000000  0.194059  0.029194  0.149028   
STR   NaN  0.055744  0.028999  0.194059  1.000000  0.027837  0.317765   
XMR   NaN  0.123248  0.084889  0.029194  0.027837  1.000000  0.028102   
XRP   NaN  0.087309  0.078307  0.149028  0.317765  0.028102  1.000000   
BTC   NaN -0.009081 -0.017667  0.094777  0.076000  0.131706  0.043544   

           BTC  
BCH        NaN  
DASH -0.009081  
ETH  -0.017667  
NXT   0.094777  
STR   0.076000  
XMR   0.131706  
XRP   0.043544  
BTC   1.000000

In [117]:
def correlation_heatmap(df, title, absolute_bounds=True):
    '''Plot a correlation heatmap for the entire dataframe'''
    heatmap = go.Heatmap(
        z=df.corr(method='pearson').as_matrix(),
        x=df.columns,
        y=df.columns,
        colorbar=dict(title='Pearson Coefficient'),
    )
    
    layout = go.Layout(title=title)
    
    if absolute_bounds:
        heatmap['zmax'] = 1.0
        heatmap['zmin'] = -1.0
        
    fig = go.Figure(data=[heatmap], layout=layout)
    py.iplot(fig)

In [118]:
correlation_heatmap(combined_df_2016.pct_change(), "Cryptocurrency Correlations in 2016")

In [119]:
combined_df_2017 = combined_df[combined_df.index.year == 2017]
combined_df_2017.pct_change().corr(method='pearson')

BCH      DASH       ETH       NXT       STR       XMR       XRP  \
BCH   1.000000  0.257470 -0.207612 -0.189671 -0.393959 -0.366116 -0.180367   
DASH  0.257470  1.000000  0.467944  0.188729  0.156888  0.416213  0.055815   
ETH  -0.207612  0.467944  1.000000  0.350870  0.223389  0.564681  0.110153   
NXT  -0.189671  0.188729  0.350870  1.000000  0.397243  0.291123  0.296876   
STR  -0.393959  0.156888  0.223389  0.397243  1.000000  0.315779  0.621200   
XMR  -0.366116  0.416213  0.564681  0.291123  0.315779  1.000000  0.228727   
XRP  -0.180367  0.055815  0.110153  0.296876  0.621200  0.228727  1.000000   
BTC  -0.180700  0.354195  0.407718  0.283892  0.177460  0.426847  0.159474   

           BTC  
BCH  -0.180700  
DASH  0.354195  
ETH   0.407718  
NXT   0.283892  
STR   0.177460  
XMR   0.426847  
XRP   0.159474  
BTC   1.000000

In [120]:
correlation_heatmap(combined_df_2017.pct_change(), "Cryptocurrency Correlations in 2017")